# PB016: Umělá inteligence I, cvičení 5 - Hry a herní strategie

Dnešní téma jsou hry, herní strategie a základní algoritmy pro optimální řešení her pomocí UI. Soustředit se budeme zejména na:
1. __Algoritmus minimax__
2. __Alfa-beta prořezávání__

---

## 1. Algoritmus [minimax](https://en.wikipedia.org/wiki/Minimax)

__Základní fakta__
- Koncept původně vycházející z [teorie her](https://en.wikipedia.org/wiki/Game_theory).
- Navržen pro hry dvou a více střídajících se hráčů, z nichž každý disponuje množinou strategií pro každý jednotlivý tah ve hře.
- Koncové stavy hry jsou ohodnoceny valuační funkcí, která přiřazuje jejich hodnotu pro každého hráče.
- Algoritmus minimax rekurzivně minimalizuje možnou prohru hráče v nejhorším možném případě (tj. případě, že se protihráč v každém tahu snaží dosáhnout naší maximální prohry výběrem optimální strategie).
- V jednoduchých hrách je možné úplné vyhodnocení hry, ale pro složitější hry rychle dochází ke kombinatorické explozi a algoritmus tudíž prohledává jen několik málo úrovní stromu možných tahů.

__Pro ilustraci__ - příklad obecného minimax stromu:

![minimax strom](https://www.fi.muni.cz/~novacek/courses/pb016/labs/img/minimax.png)

### Hra pro toto cvičení
- Piškvorky (viz. též [Tic Tac Toe](https://en.wikipedia.org/wiki/Tic-tac-toe)) na ploše 3x3.

__Příklad__ neohodnoceného herního stromu pro piškvorky:

![tictactoe strom](https://www.fi.muni.cz/~novacek/courses/pb016/labs/img/tictactoe.png)

### Základní kód hry
- třída reprezentující hrací plochu s funkcemi pro:
 - inicializaci hrací plochy,
 - ověření, zda je aktuální stav hrací plochy koncový,
 - ověření přípustnosti tahu,
 - vykreslení hrací plochy.

In [1]:
# pro mereni casu nutneho pro vyhodnoceni hry pomoci minimaxu a alfa-beta prorezavani
import time

# definice tridy pro reprezentaci hry
class Game:
    def __init__(self):
        self.initialize_game()

    # funkce pouzitelna jak k inicializaci, tak i k resetu hry
    def initialize_game(self):
        self.current_state = [['.','.','.'],
                              ['.','.','.'],
                              ['.','.','.']]
        self.result = None
        # hrac X vzdy hraje prvni
        self.player_turn = 'X'

    # test konce hry - pokud ano, vraci viteze ('X' nebo 'O'), pripadne '.', jde-li o remizu;
    #                  pokud ne, vraci None
    def is_end(self):
        # vertikalni vyhra
        for i in range(0, 3):
            if (self.current_state[0][i] != '.' and
                self.current_state[0][i] == self.current_state[1][i] and
                self.current_state[1][i] == self.current_state[2][i]):
                return self.current_state[0][i]

        # horizontalni vyhra
        for i in range(0, 3):
            if (self.current_state[i] == ['X', 'X', 'X']):
                return 'X'
            elif (self.current_state[i] == ['O', 'O', 'O']):
                return 'O'

        # vyhra na hlavni diagonale
        if (self.current_state[0][0] != '.' and
            self.current_state[0][0] == self.current_state[1][1] and
            self.current_state[0][0] == self.current_state[2][2]):
            return self.current_state[0][0]

        # vyhra na vedlejsi diagonale
        if (self.current_state[0][2] != '.' and
            self.current_state[0][2] == self.current_state[1][1] and
            self.current_state[0][2] == self.current_state[2][0]):
            return self.current_state[0][2]

        # test plnosti hraci plochy
        for i in range(0, 3):
            for j in range(0, 3):
                # neni plna, pokracujeme
                if (self.current_state[i][j] == '.'):
                    return None

        # remiza
        return '.'

    # test pripustnosti tahu
    def is_valid(self, px, py):
        if px < 0 or px > 2 or py < 0 or py > 2:
            return False
        elif self.current_state[px][py] != '.':
            return False
        else:
            return True
    
    # vypis hraci plochy
    def draw_board(self):
        for i in range(0, 3):
            print(' | '.join(self.current_state[i]))
        print()

### Funkce pro hraní hry
- Cyklus střídání tahů hráčů `'X'` a `'O'`, dokud jeden z nich nevyhraje, případně dokud nedojde k remíze.

In [2]:
def play(game):
    while True:
        game.draw_board()
        game.result = game.is_end()

        # vypis prislusne zpravy ke konci hry
        if game.result != None:
            if game.result == 'X':
                print('Vitezem je X!')
            elif game.result == 'O':
                print('Vitezem je O!')
            elif game.result == '.':
                print('Remiza!')

            game.initialize_game()
            return

        # tah hrace
        if game.player_turn == 'X':

            while True:

                # vypocet optimalniho doporuceneho tahu minimalizacnim krokem
                print('Pocitam doporuceny optimalni tah...')
                start = time.time()
                (m, qx, qy) = mini(game)
                end = time.time()
                print('Vypocet zabral %.4f ms' % (1000*(end - start),))
                print('Doporuceny tah: X = %d, Y = %d' % (qx, qy))

                correct_format, px, py = False, -1, -1
                while not correct_format:
                    try:
                        px = int(input('Zadej souradnici X: '))
                        py = int(input('Zadej souradnici Y: '))
                        correct_format = True
                    except ValueError:
                        print('Neplatny format, prosim opakuj zadani.')
                        correct_format = False

                if game.is_valid(px, py):
                    game.current_state[px][py] = 'X'
                    game.player_turn = 'O'
                    break
                else:
                    print('Neplatny tah, zkus to prosim znovu.')

        # tah UI
        else:
            (m, px, py) = maxi(game)
            game.current_state[px][py] = 'O'
            game.player_turn = 'X'

### __Příklad 1.1: Výběr tahu pro UI__
- Implementujte funkci pro výběr optimálního tahu pro UI (tj. maximalizaci koncové hodnoty hry z aktuální pozice).

In [ ]:
# hrac 'O' maximalizuje (v tomto pripade je to UI)
def maxi(game):

    # mozne hodnoty pro maximum jsou:
    # -1 - prohra
    # 0  - remiza
    # 1  - vyhra

    # pocatecni nastaveni maxima jako -2 (horsi nez nejhorsi pripad)
    maxv = -2

    px = None
    py = None

    # testovani konce hry
    result = game.is_end()

    # pokud hra skonci, funkce musi vratit vyhodnoceni daneho stavu (-1 pro prohru, 0 pro remizu, 1 pro vyhru)
    if result == 'X':
        return (-1, None, None)
    elif result == 'O':
        return (1, None, None)
    elif result == '.':
        return (0, None, None)

    # vyber souradnic pro 'O' postupnym testovanim optimality moznych tahu (tj. "vymezenim se" vuci vysledku volani funkce mini)

    # TODO - DOPLNIT SAMI
    
    # vracime hodnotu a souradnice optimalniho tahu
    return (maxv, px, py)

#### __Možné řešení výběru tahu pro UI__

In [ ]:
# hrac 'O' maximalizuje (v tomto pripade je to UI)
def maxi(game):

    # mozne hodnoty pro maximum jsou:
    # -1 - prohra
    # 0  - remiza
    # 1  - vyhra

    # pocatecni nastaveni maxima jako -2 (horsi nez nejhorsi pripad)
    maxv = -2

    px = None
    py = None

    # testovani konce hry
    result = game.is_end()

    # pokud hra skonci, funkce musi vratit vyhodnoceni daneho stavu (-1 pro prohru, 0 pro remizu, 1 pro vyhru)
    if result == 'X':
        return (-1, None, None)
    elif result == 'O':
        return (1, None, None)
    elif result == '.':
        return (0, None, None)

    # vyber souradnic pro 'O' postupnym testovanim optimality moznych tahu (tj. "vymezenim se" vuci vysledku volani funkce mini)
    for i in range(0, 3):
        for j in range(0, 3):
            # testujeme tah, pokud je pole prazdne
            if game.current_state[i][j] == '.':
                # zkousime umistit 'O' a testujeme, zda je dany tah lepsi nez aktualne optimalni
                game.current_state[i][j] = 'O'
                (m, min_i, min_j) = mini(game)
                # pripadna aktualizace optimalniho tahu a aktualniho maxima
                if m > maxv:
                    maxv = m
                    px = i
                    py = j
                # reset pole na prazdne
                game.current_state[i][j] = '.'
    
    # vracime hodnotu a souradnice optimalniho tahu
    return (maxv, px, py)

### __Příklad 1.2: Simulace výběru tahu člověka__
- Implementujte funkci pro výběr optimálního tahu pro člověka (tj. minimalizaci koncové hodnoty hry z aktuální pozice).

In [ ]:
# hrac 'X' minimalizuje (v tomto pripade je to clovek)
def mini(game):

    # mozne hodnoty pro minimum jsou:
    # -1 - vyhra
    # 0  - remiza
    # 1  - prohra

    # pocatecni nastaveni minima jako 2 (horsi nez nejhorsi pripad)
    minv = 2

    qx = None
    qy = None

    # testovani konce hry
    result = game.is_end()

    # pokud hra skonci, funkce musi vratit vyhodnoceni daneho stavu (-1 pro vyhru, 0 pro remizu, 1 pro prohru)
    if result == 'X':
        return (-1, None, None)
    elif result == 'O':
        return (1, None, None)
    elif result == '.':
        return (0, None, None)

    # vyber souradnic pro 'X' postupnym testovanim optimality moznych tahu (tj. "vymezenim se" vuci vysledku volani funkce maxi)

    # TODO - DOPLNIT SAMI

    # vracime hodnotu a souradnice optimalniho tahu
    return (minv, qx, qy)

#### __Možné řešení výběru tahu pro člověka__

In [ ]:
# hrac 'X' minimalizuje (v tomto pripade je to clovek)
def mini(game):

    # mozne hodnoty pro minimum jsou:
    # -1 - vyhra
    # 0  - remiza
    # 1  - prohra

    # pocatecni nastaveni minima jako 2 (horsi nez nejhorsi pripad)
    minv = 2

    qx = None
    qy = None

    # testovani konce hry
    result = game.is_end()

    # pokud hra skonci, funkce musi vratit vyhodnoceni daneho stavu (-1 pro vyhru, 0 pro remizu, 1 pro prohru)
    if result == 'X':
        return (-1, None, None)
    elif result == 'O':
        return (1, None, None)
    elif result == '.':
        return (0, None, None)

    # vyber souradnic pro 'X' postupnym testovanim optimality moznych tahu (tj. "vymezenim se" vuci vysledku volani funkce maxi)
    for i in range(0, 3):
        for j in range(0, 3):
            # testujeme tah, pokud je pole prazdne
            if game.current_state[i][j] == '.':
                # zkousime umistit 'X' a testujeme, zda je dany tah lepsi nez aktualne optimalni
                game.current_state[i][j] = 'X'
                (m, max_i, max_j) = maxi(game)
                # pripadna aktualizace optimalniho tahu a aktualniho minima
                if m < minv:
                    minv = m
                    qx = i
                    qy = j
                game.current_state[i][j] = '.'

    # vracime hodnotu a souradnice optimalniho tahu
    return (minv, qx, qy)

### __A hrajeme!__

In [ ]:
g = Game()
play(g)

---

## 2. [Alfa-beta prořezávání](https://en.wikipedia.org/wiki/Alpha%E2%80%93beta_pruning)

__Základní fakta__
- Optimalizace algoritmu minimax díky určení uzlů (resp. tahů) v herním stromu, které není potřeba dále prohledávat.
- Algoritmus alfa-beta prořezávání uchovává dvě hodnoty, $\alpha$ a $\beta$, které reprezentují:
 - minimální skóre, které má zaručeno maximalizující hráč,
 - maximální skóre, které má zaručeno minimalizující hráč
- Na začátku hry platí $\alpha = - \infty, \beta = \infty$ (tj. oba hráči začínají s jejich nejhorším možným skóre). 
- Kdykoli se maximální zaručené skóre minimalizujícího hráče ("beta") stane menší než minimální zaručené skóre maximalizujícího hráče ("alfa") (tj. $\beta < \alpha$), maximalizující hráč nemusí prozkoumávat tahy vycházející z aktuálního uzlu, jelikož ví, že nereprezentují optimální strategii a nebudou ve hře dosaženy.

__Pro ilustraci__ - prořezaný minimax strom z předchozího příkladu:

![alfa-beta strom](https://www.fi.muni.cz/~novacek/courses/pb016/labs/img/alphabeta.png)

### Upravená funkce pro hraní hry
- Cyklus střídání tahů hráčů `'X'` a `'O'`, dokud jeden z nich nevyhraje, případně dokud nedojde k remíze.
- Postup stejný jak před tím, jen využívá `mini` a `maxi` funkce rozšířené pro alfa-beta prořezávání.
- Namísto počátečních nekonečných hodnot pro $\alpha, \beta$ používáme $-2, 2$ (pro takto definované piškvorky to znamená de facto to stejné).

In [3]:
def play_alpha_beta(game):
    while True:
        game.draw_board()
        game.result = game.is_end()

        if game.result != None:
            if game.result == 'X':
                print('Vitezem je X!')
            elif game.result == 'O':
                print('Vitezem je O!')
            elif game.result == '.':
                print('Remiza!')


            game.initialize_game()
            return

        if game.player_turn == 'X':

            while True:
                print('Pocitam optimalni tah...')
                start = time.time()
                # upravena mini funkce s prorezavanim
                (m, qx, qy) = mini_alpha_beta(game,-2, 2)
                end = time.time()
                print('Vypocet zabral %.4f ms' % (1000*(end - start),))
                print('Doporuceny tah: X = %d, Y = %d' % (qx, qy))

                correct_format, px, py = False, -1, -1
                while not correct_format:
                    try:
                        px = int(input('Zadej souradnici X: '))
                        py = int(input('Zadej souradnici Y: '))
                        correct_format = True
                    except ValueError:
                        print('Neplatny format, prosim opakuj zadani.')
                        correct_format = False

                if game.is_valid(px, py):
                    game.current_state[px][py] = 'X'
                    game.player_turn = 'O'
                    break
                else:
                    print('Neplatny tah, zkus to prosim znovu.')

        else:
            # upravena maxi funkce s prorezavanim
            (m, px, py) = maxi_alpha_beta(game,-2, 2)
            game.current_state[px][py] = 'O'
            game.player_turn = 'X'

### __Příklad 2.1: Výběr tahu pro UI s prořezáváním__
- Implementujte funkci pro výběr optimálního tahu pro UI (tj. maximalizaci koncové hodnoty hry z aktuální pozice).
- Tentokrát ale s prořezáním stromu tahů.

In [ ]:
def maxi_alpha_beta(game, alpha, beta):
    maxv = -2
    px = None
    py = None

    result = game.is_end()

    if result == 'X':
        return (-1, None, None)
    elif result == 'O':
        return (1, None, None)
    elif result == '.':
        return (0, None, None)

    # TODO - DOPLNIT SAMI (vyber optimalniho tahu s aktualizaci alpha a ignorovanim vetvi s prilis velkym maxv)

    return (maxv, px, py)

#### __Možné řešení výběru tahu pro UI__

In [4]:
def maxi_alpha_beta(game, alpha, beta):
    maxv = -2
    px = None
    py = None

    result = game.is_end()

    if result == 'X':
        return (-1, None, None)
    elif result == 'O':
        return (1, None, None)
    elif result == '.':
        return (0, None, None)

    for i in range(0, 3):
        for j in range(0, 3):
            if game.current_state[i][j] == '.':
                game.current_state[i][j] = 'O'
                (m, min_i, min_j) = mini_alpha_beta(game, alpha, beta)
                if m > maxv:
                    maxv = m
                    px = i
                    py = j
                game.current_state[i][j] = '.'

                # dalsi dve podminky realizuji prorezani stromu tahu (jediny rozdil oproti predchozi verzi)
                if alpha >= beta:
                    return (maxv, px, py)

                if maxv > alpha:
                    alpha = maxv

    return (maxv, px, py)

### __Příklad 2.2: Simulace výběru tahu člověka s prořezáváním__
- Implementujte funkci pro výběr optimálního tahu pro člověka (tj. minimalizaci koncové hodnoty hry z aktuální pozice).
- Tentokrát ale s prořezáním stromu tahů.

In [ ]:
def mini_alpha_beta(game, alpha, beta):

    minv = 2

    qx = None
    qy = None

    result = game.is_end()

    if result == 'X':
        return (-1, None, None)
    elif result == 'O':
        return (1, None, None)
    elif result == '.':
        return (0, None, None)

    # TODO - DOPLNIT SAMI (vyber optimalniho tahu s aktualizaci beta a ignorovanim vetvi s prilis malym minv)

    return (minv, qx, qy)

#### __Možné řešení výběru tahu pro člověka__

In [5]:
def mini_alpha_beta(game, alpha, beta):

    minv = 2

    qx = None
    qy = None

    result = game.is_end()

    if result == 'X':
        return (-1, None, None)
    elif result == 'O':
        return (1, None, None)
    elif result == '.':
        return (0, None, None)

    for i in range(0, 3):
        for j in range(0, 3):
            if game.current_state[i][j] == '.':
                game.current_state[i][j] = 'X'
                (m, max_i, max_j) = maxi_alpha_beta(game, alpha, beta)
                if m < minv:
                    minv = m
                    qx = i
                    qy = j
                game.current_state[i][j] = '.'

                # dalsi dve podminky realizuji prorezani stromu tahu (jediny rozdil oproti predchozi verzi)
                if beta <= alpha:
                    return (minv, qx, qy)

                if minv < beta:
                    beta = minv

    return (minv, qx, qy)

### __A hrajeme!__

In [ ]:
g = Game()
play_alpha_beta(g)

### __K zamyšlení__
- Jak upravit kód cvičení pro větší hrací plochy, případně těžší podmínku výhry (tj. nutnost dosažení 4 a více polí v řadě)?
- Jakým způsobem tyto změny ovlivní rychlost prohledávání?

---

#### _Poznámka na závěr_ - materiály použité v tomto notebooku jsou převzatá originální díla licencovaná původními autory následujícím způsobem:
- Příklady herních stromů a kódu:
 - Převzato z webu [Stack Abuse](https://stackabuse.com/)
 - Autor: [Mina Krivokuća](mina.krivokuca@gmail.com)
 - Licence: N/A (převzato pouze pro interní použití v PB016 na FI MU s laskavým povolením autorky a Davida Landupa, provozovatele StackAbuse)